# Le tri rapide

## Version élémentaire

Marc Lorenzi

5 octobre 2022

In [ ]:
import matplotlib.pyplot as plt
from fractions import Fraction
import random
import math

Le *tri rapide* est un algorithme de tri comparatif. Cet algorithme possède de nombreux avantages, et aussi des inconvénients. 

- Il peut trier une liste *sur place*, c'est à dire en n'utilisant que la mémoire nécessaire pour stocker la liste, plus une quantité bornée de mémoire, indépendante de la longueur de la liste à trier.
- Il est extrêmement efficace pour beaucoup de listes.

L'un de ses inconvénients est que, pour certaines listes, l'algorithme de tri se comporte mal. On peut régler partiellement ce problème en effectuant une *randomisation*.

Nous aurons besoin dans la suite de faire des expériences sur le tri rapide, et en particulier de compter des comparaisons. Écrivons donc une classe `Compteur`. Une instance de cette classe est un objet qui sait compter ...

In [ ]:
class Compteur:
    
    def __init__(self): self.cpt = 0
    def incr(self): self.cpt += 1
    def reset(self): self.cpt = 0
    def __str__(self): return str(self.cpt)

In [ ]:
cptr0 = Compteur()
for k in range(10): cptr0.incr()
print(cptr0)
cptr0.reset()
print(cptr0)

## 1. Le tri rapide

### 1.1 Comparer deux nombres

La fonction `inferieur` prend en paramètres deux objets $x$ et $y$, et un compteur `cptr`. Elle incrémente le competur et renvoie `True` si $x\le y$ et `False` sinon.

In [ ]:
def inferieur(x, y, cptr):
    cptr.incr()
    return x <= y

In [ ]:
s = [1, 4, 2, 8, 5, 7]
print(inferieur(s[2], s[3], cptr0))
print(cptr0)

**Remarque.** Nous ne prouverons pas dans ce notebook la correction des deux fonctions que nous allons maintenant écrire, `partition` et `tri_rapide`.

### 1.2 Partitionner

La fonction `partition` prend en paramètres une liste $s$ et un compteur `cptr`. Soient $p=s[0]$ (le *pivot* de la partition) et $s'=s[1:]$. La fonction fabrique les listes

$$s_1=[x\in s': x\le p]$$

et 

$$s_2=[x\in s': x> p]$$

Elle renvoie le triplet $(p, s_1, s_2)$. Le compteur `cptr` est incrémenté à chaque comparaison du pivot $p$ avec un élément $x$ de $s$.

In [ ]:
def partition(s, cptr):
    n = len(s)
    s1 = []
    s2 = []
    p = s[0]
    for x in s[1:]:
        if inferieur(x, p, cptr): s1.append(x)
        else: s2.append(x)
    return (p, s1, s2)

In [ ]:
cptr0.reset()
print(partition([4, 1, 2, 8, 5, 7], cptr0))
print(cptr0)

### 1.3 Trier

Le tri rapide est un algorithme du type « diviser pour régner ».

La fonction `tri_rapide` prend en paramètres une liste $s$ et un compteur.

- Si $s$ est vide, alors $s$ est triée. La fonction renvoie la liste vide.
- Sinon, la fonction appelle la fonction `partition`, qui renvoie un pivot $p$ et deux sous-listes $s_1$ et $s_2$ de $s$ (« diviser »). Puis elle se rappelle récursivement $s_1$ et $s_2$ et, pour terminer, regroupe le tout (« régner »).

Soyons, clairs, ceci n'est pas une version « propre » du tri rapide. Notre fonction a la bonne complexité temporelle, mais elle a une complexité spatiale en $O(n)$, alors que l'on peut atteindre une complexité en $O(1)$.

In [ ]:
def tri_rapide(s, cptr):
    if s == []: return []
    else:
        (p, s1, s2) = partition(s, cptr)
        s3 = tri_rapide(s1, cptr)
        s4 = tri_rapide(s2, cptr)
        return s3 + [p] + s4

In [ ]:
cptr0.reset()
s = tri_rapide([1, 4, 2, 8, 5, 7], cptr0)
print(s)
print(cptr0)

## 2. Expériences statistiques

### 2.1 Listes aléatoires

Pour faire des tests, nous aurons besoin de créer des listes aléatoires. La fonction `liste_aleatoire` prend en paramètre un entier $n$ et ranvoie une permutation aléatoire de la liste des entiers entre 0 et $n-1$. Elle utilise l'algorithme de Fisher-Yates.

In [ ]:
def liste_aleatoire(n):
    s = list(range(n))
    for i in range(n):
        j = random.randint(0, i)
        s[i], s[j] = s[j], s[i]
    return s

Effectuons un tri rapide sur une liste aléatoire de longueur 20.

In [ ]:
s = liste_aleatoire(20)
print(s)
cptr0.reset()
print(tri_rapide(s, cptr0))
print(cptr0)

### 2.2 Nombre moyen de comparaisons

La fonction `stats` prend en paramètres deux entiers $n$ et $m$. Elle effectue $m$ tris rapides de listes aléatoires de taille $n$, et renvoie le nombre moyen de comparaisons d'éléments de listes.

In [ ]:
def stats(n, m):
    cptr = Compteur()
    for k in range(m):
        s = tri_rapide(liste_aleatoire(n), cptr)
    return cptr.cpt / m

Voici une évaluation du nombre moyen de comparaisons d'éléments de listes nécessaires pour trier une liste de longueur 100.

In [ ]:
print(stats(100, 1000))

Pour trier une liste de longueur 100, le tri rapide effectue « en moyenne » 650 comparaisons.

Confrontons maintenant les résultats de nos expérience à la théorie.

## 2. La théorie

**NB :** Dans toute la suite, lorsque nous parlerons de *comparaisons*, nous sous-entendrons qu'il s'agit de comparaisons *d'éléments de listes*.

### 2.1 Le nombre moyen de comparaisons

Soit $n\in\mathbb N$. Soit $C_n$ le nombre moyen de comparaisons nécessaire pour trier une liste de taille $n$. Que vaut $C_n$ ? Pour répondre rigoureusement à cette question, il conviendrait d'introduire des espaces probabilisés et des variables aléatoires. Nous allons nous contenter d'arguments plus intuitifs (mais pas très rigoureux).

Le tri rapide ne fait aucune comparaison lorsqu'on lui demande de trier la liste vide. On a donc $C_0=0$.

Si $n\ge 1$, la fonction `tri_rapide` appelle `partition` qui effectue $n-1$ comparaisons. Puis, la fonction de tri se rappelle sur deux sous-listes $s_1$ et $s_2$ de la liste initiale. Quelles sont les tailles de $s_1$ et $s_2$ ? Ces deux listes forment une partition (eh oui !) de la liste d'origine privée du pivot. Si nous notons $k=|s_1|$, alors $|s_2|=n-1-k$. L'entier $k$ peut *a priori* prendre toutes les valeurs possibles entre 0 et $n-1$. Pour trier $s_1$, le tri rapide effectue « en moyenne » $C_k$ comparaisons. Pour trier $s_2$, le tri rapide effectue « en moyenne » $C_{n-1-k}$ comparaisons. Sans aucune rigueur, nous lançons l'idée que pour obtenir la valeur de $C_n$ il suffit de faire la moyenne sur toutes les valeurs possibles de $k$. On a alors

$$C_n=n-1+\frac 1 n\sum_{k=0}^{n-1}(C_k+C_{n-1-k})$$

On peut encore écrire

$$C_n=n-1+\frac 1 n\sum_{k=0}^{n-1}C_k+\frac 1 n\sum_{k=0}^{n-1}C_{n-1-k}$$

Les deux sommes sont égales (poser $k'=n-1-k$ dans la seconde somme). On a donc

$$C_n=n-1+\frac 2 n\sum_{k=0}^{n-1}C_k$$

**Remarque.** L'approche rigoureuse consiste à considérer l'espace probabilisé $(\mathfrak S_n, \mathbb P)$ où $\mathfrak S_n$ est l'ensemble des permutations de l'ensemble $[|0,n-1|]$ et $\mathbb P$ est la probabilité uniforme. On définit ensuite la variable aléatoire $X_n:\mathfrak S_n\to\mathbb N$ qui à toute permutation $\sigma$ associe le nombre de comparaisons effectuées par `tri_rapide` pour trier la liste $[\sigma(0),\ldots,\sigma(n-1)]$. On a alors

$$C_n=E(X_n)$$

où $E$
 est l'espérance. On peut alors montrer rigoureusement que $C_n$ vérifie la relation de récurrence ci-dessus.

### 2.2 Une fonction qui calcule $C_n$

La relation de récurrence ci-dessus donne immédiatement une fonction qui calcule $C_n$. La complexité en temps de cette fonction est $O(n)$. Mais remarquons que sa complexité en espace est aussi $O(n)$. Soyons donc raisonnables. 

La fonction `C` possède un paramètre optionnel `exact`. Si ce paramètre vaut `True`, la fonction renvoie la valeur exacte du rationnel $C_n$. Sinon, elle renvoie une valeur approchée de type flottant.

In [ ]:
def C(n, exact=False):
    if exact:
        cs = (n + 1) * [Fraction(0)]
        for k in range(1, n + 1):
            cs[k] = k - 1 + Fraction(2, k) * sum(cs[:k])
        return cs[n]
    else:
        cs = (n + 1) * [0]
        for k in range(1, n + 1):
            cs[k] = k - 1 + 2 * sum(cs[:k]) / k
        return cs[n]

In [ ]:
for n in range(11):
    print('%3d %10s %10.6f' % (n, C(n, exact=True), C(n, exact=False)))

Histoire de comparer avec nos expériences statistiques ...

In [ ]:
print(stats(10, 10000))

### 2.3 Une expression simplifiée de $C_n$

Soit $n\ge 2$. On a 

$$nC_n-(n-1)C_{n-1}=n(n-1)+2\sum_{k=0}^{n-1}C_k-(n-1)(n-2)-2\sum_{k=0}^{n-2}C_k=2(n-1)+2C_{n-1}$$

De là,

$$nC_n=2(n-1)+(n+1)C_{n-1}$$

Remarquons que cette égalité est encore vraie pour $n=1$. Posons maintenant, pour tout $n\in\mathbb N$,

$$u_n=\frac{C_n}{n+1}$$

On a $u_0=0$ et, pour tout $n\ge 1$,

$$u_n=2\frac{n-1}{n(n+1)}+u_{n-1}$$

Il en résulte, par une récurrence facile, que pour tout $n\ge 1$,

$$u_n=2\sum_{k=1}^{n}\frac{k-1}{k(k+1)}$$

Pour calculer cette somme, faisons une décomposition en éléments simples. On a pour tout $k\ge 1$,

$$\frac{k-1}{k(k+1)}=- \frac 1 k + \frac 2 {k+1}$$

De là, pour tout $n\ge 1$,

$$\sum_{k=1}^{n}\frac{k-1}{k(k+1)}=-\sum_{k=1}^n\frac 1 k+2\sum_{k=1}^n\frac 1 {k+1}$$

Faisons intervenir le $n$ième *nombre harmonique*

$$H_n=\sum_{k=1}^n\frac 1 k$$

Remarquons que

$$\sum_{k=1}^n\frac 1 {k+1}=\sum_{k=2}^{n+1}\frac 1 {k}=H_n+\frac 1{n+1}-1=H_n-\frac{n}{n+1}$$

On a donc

$$u_n=2H_n-\frac {4n}{n+1}$$

et finalement

$$C_n=2(n+1)H_n-4n$$

La complexité temporelle du calcul de $C_n$ par cette formule est toujours $O(n)$ mais, cette fois-ci, la complexité spatiale est $O(1)$.

In [ ]:
def H(n, exact=False):
    s = 0
    for k in range(1, n + 1):
        if exact: s += Fraction(1, k)
        else: s += 1 / k
    return s

In [ ]:
H(10000)

In [ ]:
def C2(n):
    return 2 * (n + 1) * H(n) - 4 * n

Les fonctions `C` et `C2` doivent évidemment toujours renvoyer la même valeur.

In [ ]:
print(C(1000))
print(C2(1000))

### 2.4 Un développement asymptotique de $C_n$

Remarquons que le $n$ième nombre harmonique possède un développement asymptotique intéressant.

$$H_n=\ln n+\gamma+\frac 1 {2n}+o\left(\frac 1 n\right)$$

où $\gamma\simeq 0.577215644$ est la *constante d'Euler*. On a donc

$$C_n=2(n+1)\ln n + 2(n+1)\gamma - 4n + 2\frac {n+1}{2n} + o(1)$$

qui se simplife en

$$C_n=2(n+1)\ln n +2(\gamma-2)n + 2\gamma + 1+o(1)$$

Notre fonction d'approximation de $C_n$ a évidemment une complexité temporelle en $O(1)$ et une complexité spatiale en $O(1)$.

In [ ]:
def approx_C(n):
    gamma = 0.577215644
    return 2 * (n + 1) * math.log(n) + 2 * (gamma - 2) * n + 2 * gamma + 1

In [ ]:
print(C2(100))
print(approx_C(100))

Ci-dessous, un graphique montrant l'évolution de la différence entre $C_n$ et son approximation. Cette différence tend vers 0 lorsque $n$ tend vers l'infini, et elle n'est jamais supérieure à 1.

In [ ]:
plt.rcParams['figure.figsize'] = (10, 5) 

In [ ]:
ns = list(range(1, 100))
cs = [C2(n) - approx_C(n) for n in ns]
plt.plot(ns, cs, 'k')
plt.grid()

## 3. Le pire cas du tri rapide

Pour toute liste $s$, notons $C(s)$ le nombre de comparaisons effectuées par le tri rapide pour trier une liste de taille $n$. Notons également, pour tout $n\in\mathbb N$,

$$U_n=\max\{C(s):|s|=n\}$$

où $|s|$ est la longueur de la liste $s$.

### 3.1 Une minoration

Que se passe-t-il lorsqu'on partitionne une liste triée dans l'ordre croissant ?

In [ ]:
partition(range(10), cptr0)

Et dans l'ordre décroissant ?

In [ ]:
partition(range(10, -1, -1), cptr0)

Notons $V_n$ le nombre de comparaisons effectuées par `tri_rapide` lors du tri d'une liste $s$ de taille $n$ triée dans l'ordre croissant. Si $n\ge 1$, l'appel à `partition` renvoie la liste vide et la liste $s'=[s_1,\ldots,s_{n-1}]$, toujours triée dans l'ordre croissant. Les appels récursifs à `tri_rapide` nécessitent, pour l'appel sur la liste $[]$, 0 comparaison, et pour l'appel sur $s'$, $V_{n-1}$ comparaisons. Ainsi, pour tout $n\ge 1$,

$$V_n=n-1+V_{n-1}$$

Comme $V_0=0$, une récurrence immédiate montre que pour tout $n\in\mathbb N$,

$$V_n=\frac 1 2n(n-1)$$

Pour toute liste $s$ de longueur $n$, on a $C(s)\le U_n$. On a donc $V_n\le U_n$, d'où

$$U_n\ge\frac 1 2n(n-1)$$

### 3.2 Une majoration

On a évidemment $U_0=0$. Soit $s$ une liste de longueur $n\ge 1$. Appelons `tri_rapide` sur la liste $s$. Après que `partition` ait effectué $n-1$ comparaisons, la fonction `tri_rapide` se rappelle sur une liste de taille $k$ et une liste de taille $n-1-k$, où $0\le k\le n-1$. On a donc

$$\begin{array}{lll}
C(s)&\le& n - 1 + U_k+U_{n-1-k}\\
&\le&n - 1 + \max\{U_k+U_{n-1-k}:0\le k\le n-1\}\\
\end{array}$$

Le majorant obtenu ci-dessus ne dépend pas de $s$, mais uniquement de $n$. Il en résulte que

$$U_n\le n - 1 + \max\{U_k+U_{n-1-k}:0\le k\le n-1\}$$

La fonction `U` prend en paramètre un entier $n$ et renvoie $[U_0,\ldots,U_n]$, où plutôt ce que seraient ces nombres si l'inégalité ci-dessus était une égalité. Nous verrons bientôt que c'est le cas.

In [ ]:
def U(n):
    s = (n + 1) * [0]
    for m in range(1, n + 1):
        s[m] = m - 1 + max([s[k] + s[m - 1 - k] for k in range(m)])
    return s

In [ ]:
print(U(10))

Considérons la fonction $f:[0,n-1]\to\mathbb R$ définie par

$$f(x)=g(x)+g(n-1-x)$$

où $g(x)=x(x-1)$. Voici le graphe de $f$.

In [ ]:
def g(x):
    return x * (x - 1)

In [ ]:
def f(x, n):
    return g(x) + g(n - 1 - x)

In [ ]:
def tracer_f(n):
    xs = [k / 500 * (n - 1) for k in range(501)]
    ys = [f(x, n) for x in xs]
    plt.plot(xs, ys, 'k')
    plt.grid()

In [ ]:
tracer_f(5)

La fonction $f$ est dérivable sur $[0,n-1]$. On a pour tout $x\in[0,n-1]$, 

$$f'(x)=g'(x)-g'(n-1-x)=2x-1-2(n-1-x)+1=2(2x-(n-1))$$

On en déduit les variations de $f$. Le maximum de $f$ est atteint en 0 et $n-1$, et vaut $(n-1)(n-2)$.

**Proposition.** Pour tout $n\in\mathbb N$,

$$U_n\le \frac 1 2 n (n -1)$$

**Démonstration.** Prouvons le résultat par récurrence forte sur $n$. C'est clair pour $n=0$. Soit $n\ge 1$. Supposons que pour tout $k<n$, on ait $U_k\le \frac 1 2 k (k-1)$. On a alors

$$\begin{array}{lll}
U_n&\le& n - 1 + \max\{U_k+U_{n-1-k}:0\le k\le n-1\}\\
&\le&n - 1 + \frac 1 2\max\{k(k-1)+(n-1-k)(n-2-k):0\le k\le n-1\}\\
&=&n - 1 + \frac 1 2\max\{f(k):0\le k\le n-1\}\\
&\le&n-1+\frac 1 2 (n-1)(n-2)\\
&=&\frac 1 2 n(n-1)
\end{array}$$


### 3.3 Conclusion

Nous venons ainsi de prouver que pour tout $n\in\mathbb N$,

$$U_n=\frac 1 2n(n-1)$$

Remarquons, bien que cela ne soit plus très utile, que ceci entraîne, pour tout $n\ge 1$,

$$U_n= n - 1 + \max\{U_k+U_{n-1-k}:0\le k\le n-1\}$$

Le tri rapide a donc un très bon comportement en moyenne (on peut prouver, mais ceci est une autre histoire, qu'un tri comparatif nécessite au minimum de l'ordre de $n\ln n$ opérations pour trier des listes de longueur $n$). En revanche, son comportement pour certaines listes (les listes déjà triées, en particulier), est mauvais.

## 4. Randomisation

Un remède à ce problème consiste à *randomiser* l'algorithme. Avant d'appeler `partition`, on échange le premier élément de la liste avec un autre élément, pris au hasard. L'étude de cet algorithme randomisé dépasse évidemment le cadre du notebook. La fonction de tri devient ainsi

In [ ]:
def tri_rapide_rand(s, cptr):
    if s == []: return []
    else:
        k = random.randint(0, len(s) - 1)
        s[0], s[k] = s[k], s[0]
        (p, s1, s2) = partition(s, cptr)
        s3 = tri_rapide_rand(s1, cptr)
        s4 = tri_rapide_rand(s2, cptr)
        return s3 + [p] + s4

Pour prendre un exemple, voici le nombre de comparaisons effectuées par `tri_rapide`et `tri_rapide_rand` pour trier une liste « presque triée ».

In [ ]:
def liste_presque_triee(n):
    s = list(range(n))
    for k in range(math.ceil(math.log(n + 1))):
        i, j = random.randint(0, n - 1), random.randint(0, n - 1)
        s[i], s[j] = s[j], s[i]
    return s

In [ ]:
print(liste_presque_triee(20))

In [ ]:
cptr0.reset()
s = liste_presque_triee(3000)
s1 = tri_rapide(s, cptr0)
print(cptr0)
cptr0.reset()
s1 = tri_rapide_rand(s, cptr0)
print(cptr0)

Le gain apporté par l'algorithme randomisé est énorme. L'algorithme randomisé, quant à lui, reste efficace même pour des listes de grande taille. Une liste presque triée de 100000 éléments ne lui fait pas peur.

In [ ]:
cptr0.reset()
s = liste_presque_triee(100000)
s1 = tri_rapide_rand(s, cptr0)
print(cptr0)

Remarquons que le nombre de comparaisons effectuées par l'algorithme randomisé est de l'ordre du nombre moyen de comparaisons du tri rapide.

In [ ]:
approx_C(100000)

Terminons par une remarque d'ordre philosophique. Le nombre de comparaisons effectuées par l'algorithme randomisé dépend de l'instant où l'on effectue le tri. La quantité $C(s)$ que nous avions définie plus haut n'a donc plus de sens. À un instant donné, le nombre de listes pour lesquelles l'algorithme randomisé a un mauvais comportement est le même que pour l'algorithme déterministe. Mais ces « mauvaises listes » ne sont jamais les mêmes, et elles dpendent du générateur de nombres pseudo-aléatoire utilisé. Sauf à le faire exprès, par exemple en « piratant » le générateur de nombres aléatoires, on ne tombera jamais sur une telle liste. Enfin, presque jamais ... ce « presque » est évidemment relativement angoissant pour des logiciels dont la fiabilité implique des vies humaines.